# .dat to .csv
The purpose of this tool is to convert _.dat_ files into _.csv_ files where each row is a sample to be analyzed.

The .dat files are obtained by running the *cap2dat* program on _.pcap_ files.

Firstly the data is loaded to a numpy array.

In [2]:
import os
import numpy as np
from collections import defaultdict, deque
from scalogram import *
import pandas as pd
from sklearn.externals import joblib 
import re

base_url = '../../../shared/'
sampling_interval = '01s' # 1s or 01s
sample_size = 30 # number of intervals for each sample
all_data = np.zeros(5)

def split_number(s):
    return list(filter(None, re.split(r'(\d+)', s)))

for path, subdirs, files in os.walk(base_url):
    for name in files:
        if os.path.basename(path) != sampling_interval:
            continue
        
        print(os.path.join(path, name))
        
        #[up_n_packets, up_n_bytes, up_flag, down_n_packets, down_n_bytes, down_flag]
        data = np.loadtxt(os.path.join(path, name))
        data = np.delete(data, [2,5], 1)
        label = np.full((np.size(data, 0), 1), split_number(name.split('.')[0])[0])
        data = np.hstack((data, label))
        all_data = np.vstack((all_data, data))

../../../shared/openvpn/netflix/dat/01s/netflix-openvpn.pcapng_0.10s.dat
../../../shared/openvpn/youtube/dat/01s/youtube-openvpn.pcapng_0.10s.dat
../../../shared/openvpn/acestream/dat/01s/acestream-openvpn.pcapng_0.10s.dat
../../../shared/openvpn/twitch/dat/01s/twitch-openvpn.pcapng_0.10s.dat
../../../shared/normal/netflix/dat/01s/netflix4.pcapng_0.10s.dat
../../../shared/normal/netflix/dat/01s/netflix10.pcapng_0.10s.dat
../../../shared/normal/netflix/dat/01s/netflix11.pcapng_0.10s.dat
../../../shared/normal/netflix/dat/01s/netflix.pcapng_0.10s.dat
../../../shared/normal/netflix/dat/01s/netflix2.pcapng_0.10s.dat
../../../shared/normal/netflix/dat/01s/netflix12.pcapng_0.10s.dat
../../../shared/normal/netflix/dat/01s/netflix3.pcapng_0.10s.dat
../../../shared/normal/youtube/dat/01s/youtube2.pcapng_0.10s.dat
../../../shared/normal/youtube/dat/01s/youtube3.pcapng_0.10s.dat
../../../shared/normal/youtube/dat/01s/youtube51.pcapng_0.10s.dat
../../../shared/normal/youtube/dat/01s/youtube53.pcap

# Normalize

Apply a standard scaler to all of the data and save it (we will need it for live classification).

In [3]:
from sklearn.preprocessing import StandardScaler

to_scale = all_data[:, :-1]
scaler = StandardScaler()
scaled = scaler.fit_transform(np.asarray(to_scale))
scaled = np.hstack((scaled.astype(float), np.matrix(all_data[:, -1]).T))
joblib.dump(scaler, '../models/std_scaler_' + sampling_interval + '_' + str(sample_size) + '.sav')


/home/agro/work/thesis/env/lib/python3.6/site-packages/sklearn/utils/validation.py:475: DataConversionWarning: Data with input dtype <U32 was converted to float64 by StandardScaler.
  warnings.warn(msg, DataConversionWarning)


['../models/std_scaler_01s_30.sav']

In [4]:
zeros = scaled[0].tolist()[0][:-1]
zeros = [float(i) for i in zeros]
zeros

[-0.23530404751488543,
 -0.09876013147215375,
 -0.20622342096447888,
 -0.22861620982870556]

# Divide data into chunks

In [5]:
def get_info(data):
    info = []
    up = defaultdict(list)
    down = defaultdict(list)
    result = {}
    count = 0
    current_label = data[1, 4]
    for interval_unit in data[1:]:
        if current_label != interval_unit.item(4):
            current_label = interval_unit.item(4)
        up['packet_count'].append(float(interval_unit.item(0)))
        up['byte_count'].append(float(interval_unit.item(1)))
        down['packet_count'].append(float(interval_unit.item(2)))
        down['byte_count'].append(float(interval_unit.item(3)))
        count+=1
        if count >= sample_size:
            result['up'] = up
            result['down'] = down
            info.append((result, current_label))
            up = defaultdict(list)
            down = defaultdict(list)
            result = {}
            count = 0
    return info
info = get_info(scaled)

# Scalogram scales

In [6]:
#Scalogram
N = sample_size
dj=1/128
s0=2
J=1/dj * np.log2(0.5*N/s0)
scales=s0*2**(np.arange(J)*dj)

Get scalogram data

In [ ]:
from scipy.signal import argrelextrema

def calc_scalogram(data, scales):
    S,scales= scalogramCWT(data,scales)
    return S
def show_scalo(data, scales, colors):
    for i in range (0, len(data)):
        plt.plot(scales, data[i], colors[i], lw=3)
    plt.show()
    
# Get top X spikes from scalogram, sorted by value
def get_spikes(scalo, comparator):
    len(scalo)
    spikes = deque([(-1,-1)] * 5, maxlen=5)
    #aux = argrelextrema(scalo, comparator, order=int(len(scalo)/10))
    aux = argrelextrema(scalo, comparator)
    if aux[0].size:
        for x in np.nditer(aux) or []:
            spikes.append((scalo[x], scales[x]))
    ordered = sorted(spikes, key=lambda x: x[1], reverse=True)
    values = np.hstack(zip(*ordered))
    return values

scalos_up = []
scalos_down = []
for sample in info:
    print(sample)
    scalos_up.append(
        (
            (calc_scalogram((sample[0]['up']['byte_count']), scales), 
             calc_scalogram(np.asarray(sample[0]['up']['packet_count']), scales)
            ),
             sample[1]
        )
    )
    scalos_down.append(
        (    
            (calc_scalogram(np.asarray(sample[0]['down']['byte_count']), scales),
             calc_scalogram(np.asarray(sample[0]['down']['packet_count']), scales)
            ),
            sample[1]
        )
    )

({'up': defaultdict(<class 'list'>, {'packet_count': [4.363237189393859, 11.377961110102111, 15.119147201146514, 2.2588200131813827, 4.441178566290618, 25.173584820828346, 16.21032647770113, 15.664736839423822, 1.9470545055943491, 2.1029372593878657, 0.07646146007214807, 9.195602556992878, 19.95151256874553, 25.173584820828346, 7.948540526644744, 3.116175159045725, 4.830885450774409, 5.844123350432268, 12.391199009759971, 23.53681590599642, 14.027967924591897, 4.441178566290618, 10.208840456650735, 2.88235102835545, 1.2455821135235237, 3.116175159045725, 20.02945394564229, 22.757402137028834, 2.6485268976651746, 2.8044096514586916], 'byte_count': [21.028874012386204, 50.827709082281785, 70.44605217937693, 10.820349144957943, 21.386969506349907, 116.64037090069436, 75.45938909486875, 72.95272063712285, 9.927913699511475, 10.644104687438876, 1.3336218443826502, 43.23079463813567, 92.6479728051264, 116.64037090069436, 37.50126673471645, 15.299346108966988, 23.17744697616841, 27.8326883976

({'up': defaultdict(<class 'list'>, {'packet_count': [1.1676407366267654, 0.15440283696890647, 1.323523490420282, -0.23530404751488543, -0.15736267061812706, 2.0249958824911074, 0.9338166059364902, 1.4794062442137987, 0.7779338521429734, 1.4014648673170405, 1.1676407366267654, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, 1.4794062442137987, 2.7264682745619333, 1.8691131286975906, 2.4147027669748993, 1.9470545055943491, 0.3882269676591816, 0.7779338521429734, 0.699992475246215, 0.15440283696890647, 1.5573476211105572, 0.46616834455594, -0.15736267061812706, -0.23530404751488543, 0.9338166059364902, 1.6352889980073155, 0.3882269676591816], 'byte_count': [6.346958759874464, 1.6917173383463513, 7.063149747801866, -0.09876013147215375, 0.25933536249154726, 10.286009193475175, 5.272672277983361, 7.779340735729268, 4.556481290055959, 7.421245241765567, 6.346958759874464, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, 7.779340735729268, 11.07910925231097

({'up': defaultdict(<class 'list'>, {'packet_count': [2.0249958824911074, 2.336761390078141, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, 1.8691131286975906, 1.1676407366267654, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.07942129372136868], 'byte_count': [10.286009193475175, 11.71839116932998, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375

({'up': defaultdict(<class 'list'>, {'packet_count': [-0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, 1.4014648673170405, 2.88235102835545, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.0014799168246102958, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543], 'byte_count': [-0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, 7.421245241765567, 14.225059627075886, -0.098760131472

({'up': defaultdict(<class 'list'>, {'packet_count': [1.7911717518008323, 0.15440283696890647, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.07942129372136868, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, 1.2066114250751445, -0.19633335906650623, -0.23530404751488543, -0.23530404751488543, 2.7264682745619333, 0.3882269676591816, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.15736267061812706, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543], 'byte_count': [9.211722711584072, 1.6917173383463513, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, 0.1966208302276521, -0.09876013147215375, 

...

({'up': defaultdict(<class 'list'>, {'packet_count': [-0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.15736267061812706, 0.5441097214526983, 1.0117579828332486, 1.4794062442137987, 2.180878636284624, 1.5573476211105572, 1.9470545055943491, 1.5573476211105572, 0.8558752290397318, 0.46616834455594, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, 0.6220510983494567, -0.07942129372136868], 'byte_count': [-0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.009483607051474193, 0.7940051127346418, 1.3296642592587191, 1.8653234057827965, 2.6688121255689126, 1.9545999302034762, 2.400982552306874, 1.9545999302034762, 1.15111121041736, 0.7

({'up': defaultdict(<class 'list'>, {'packet_count': [-0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.15736267061812706, 0.5441097214526983, -0.15736267061812706, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, 0.6220510983494567, 1.2455821135235237, 0.7779338521429734, 0.9338166059364902, 2.336761390078141, 2.6485268976651746, 1.8691131286975906, 1.7132303749040738, 0.8558752290397318, 1.2455821135235237, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.15736267061812706, 0.5441097214526983, -0.15736267061812706], 'byte_count': [-0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.009483607051474193, 0.7940051127346418, -0.009483607051474193, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.098760

({'up': defaultdict(<class 'list'>, {'packet_count': [-0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.15736267061812706, 1.0117579828332486, 0.9338166059364902, 0.46616834455594, 0.7779338521429734, 2.6485268976651746, 4.363237189393859, 1.0896993597300069, -0.23530404751488543, 4.597061320084134, 2.5705855207684163, -0.23530404751488543, 0.23234421386566484, 0.46616834455594, 1.4014648673170405, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.15736267061812706, 3.6617647973230336, 2.8044096514586916], 'byte_count': [-0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.009483607051474193, 1.3296642592587191, 1.2403877348380394, 0.7047285883139622, 1.0618346859966805, 3.2044712720929898, 5.16855480934794, 1.388473

({'up': defaultdict(<class 'list'>, {'packet_count': [0.6220510983494567, 2.0249958824911074, 2.4926441438716576, 2.336761390078141, 1.7911717518008323, 2.4926441438716576, 2.180878636284624, 1.4794062442137987, 1.8691131286975906, -0.15736267061812706, -0.23530404751488543, -0.23530404751488543, -0.15736267061812706, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, 0.6220510983494567, 0.46616834455594, 0.46616834455594, 2.88235102835545, 2.88235102835545, 2.336761390078141], 'byte_count': [0.8832816371553213, 2.4902590767275536, 3.025918223251631, 2.8473651744102715, 2.2224295034655146, 3.025918223251631, 2.6688121255689126, 1.8653234057827965, 2.3117060278861943, -0.009483607051474193, -0.09876013147215375, -0.09876013147215375, 0.15688007960817707, -0.09876013147215375, -0.09876013147215375, -

({'up': defaultdict(<class 'list'>, {'packet_count': [2.336761390078141, 1.6352889980073155, -0.0014799168246102958, 0.699992475246215, -0.23530404751488543, -0.23530404751488543, -0.15736267061812706, 0.5441097214526983, -0.15736267061812706, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.23530404751488543, -0.15736267061812706, 1.0117579828332486, 0.9338166059364902, 1.4794062442137987, 2.4147027669748993, 1.8691131286975906, 2.2588200131813827, 1.9470545055943491, 1.0896993597300069, 0.6220510983494567, -0.15736267061812706, -0.23530404751488543], 'byte_count': [2.8473651744102715, 2.042675987136563, 0.16906944178988492, 0.9725581615760008, -0.09876013147215375, -0.09876013147215375, -0.009483607051474193, 0.7940051127346418, -0.009483607051474193, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.09876013147215375, -0.098760131472153

In [ ]:
local_max_up_bytes = []
local_min_up_bytes = []
local_max_up_packet = []
local_min_up_packet = []
local_max_down_bytes = []
local_min_down_bytes = []
local_max_down_packet = []
local_min_down_packet = []

for scalo in scalos_up:
    local_max_up_bytes.append((get_spikes(scalo[0][0], np.greater), scalo[1]))
    local_min_up_bytes.append((get_spikes(scalo[0][0], np.less), scalo[1]))
    local_max_up_packet.append((get_spikes(scalo[0][1], np.greater), scalo[1]))
    local_min_up_packet.append((get_spikes(scalo[0][1], np.less), scalo[1]))

for scalo in scalos_down:
    local_max_down_bytes.append((get_spikes(scalo[0][0], np.greater), scalo[1]))
    local_min_down_bytes.append((get_spikes(scalo[0][0], np.less), scalo[1]))
    local_max_down_packet.append((get_spikes(scalo[0][1], np.greater), scalo[1]))
    local_min_down_packet.append((get_spikes(scalo[0][1], np.less), scalo[1]))

In [ ]:
from itertools import groupby
from scipy import stats

def get_stats_numpy(data, zero):
    mean = np.mean(data)
    median = np.median(data)
    std = np.std(data)
    var = np.var(data)
    skew = stats.skew(data)
    kurt = stats.kurtosis(data)
    pc = [25,50,75,90]
    percentiles = np.array(np.percentile(data, pc))
    silences = np.count_nonzero(np.asarray(data)==zero)
    silence_mean = np.mean(list(sum(1 for _ in g) for k, g in groupby(data) if k==zero ))
    longest_silence = max(sum(1 for _ in g) for k, g in groupby(data) if k==zero) if silences > 0 else 0
    shortest_silence = min(sum(1 for _ in g) for k, g in groupby(data) if k==zero) if silences > 0 else 0
    
    #print("Mean: " + str(mean))
    #print("Media: " + str(median))
    #print("StdDev: " + str(std))
    #print("Variance: " + str(var))
    #print("Skewness: " + str(skew))
    #print("Kurtosis: " + str(kurt))
    #print("Pc25: " + str(percentiles[0]))
    #print("Pc50: " + str(percentiles[1]))
    #print("Pc75: " + str(percentiles[2]))
    
    features = np.hstack((mean, median, std, var, skew, kurt, percentiles, silences, silence_mean, longest_silence, shortest_silence))

    return features

# Put it all on a numpy array
def get_features_numpy(info, local_max_up_bytes, local_min_up_bytes, local_max_up_packet, local_min_up_packet, 
                       local_max_down_bytes, local_min_down_bytes, local_max_down_packet, local_min_down_packet, zeros):
    np.set_printoptions(suppress=True)

    result = []

    print(info[0][1])
    
    for idx in range(0, len(info)):
        result.append(
            np.hstack(
                (
                 get_stats_numpy(info[idx][0]['up']['byte_count'], zeros[1]),
                 get_stats_numpy(info[idx][0]['up']['packet_count'], zeros[0]),
                 local_max_up_bytes[idx][0], local_min_up_bytes[idx][0],
                 local_max_up_packet[idx][0], local_min_up_packet[idx][0],
                 get_stats_numpy(info[idx][0]['down']['byte_count'], zeros[3]),
                 get_stats_numpy(info[idx][0]['down']['packet_count'], zeros[2]),
                 local_max_down_bytes[idx][0], local_min_down_bytes[idx][0],
                 local_max_down_packet[idx][0], local_min_down_packet[idx][0],
                 info[idx][1]
                )
            )
        )
    print(len(result[0]))
    return result

In [ ]:
len(local_max_down_bytes[0])

In [ ]:
samples = get_features_numpy(info, local_max_up_bytes, local_min_up_bytes, local_max_up_packet, local_min_up_packet,
                                    local_max_down_bytes, local_min_down_bytes, local_max_down_packet, local_min_down_packet,
                                    zeros)
samples

In [ ]:
names = [
            'up_bytes_mean', 'up_bytes_median', 'up_bytes_std', 'up_bytes_var', 'up_bytes_skew', 'up_bytes_kurt',
            'up_bytes_perc25', 'up_bytes_perc50', 'up_bytes_perc75', 'up_bytes_perc90',
            'up_bytes_silences', 'up_bytes_silence_mean', 'up_bytes_longest_silence', 'up_bytes_shortest_silence',
            'up_packet_mean', 'up_packet_median', 'up_packet_std', 'up_packet_var', 'up_packet_skew', 'up_packet_kurt',
            'up_packet_perc25', 'up_packet_perc50', 'up_packet_perc75', 'up_packet_perc90',
            'up_packet_silences', 'up_packet_silence_mean', 'up_packet_longest_silence', 'up_packet_shortest_silence',
            'up_bytes_1max_y', 'up_bytes_2max_y', 'up_bytes_3max_y', 'up_bytes_4max_y', 'up_bytes_5max_y',
            'up_bytes_1max_x', 'up_bytes_2max_x', 'up_bytes_3max_x', 'up_bytes_4max_x', 'up_bytes_5max_x',
            'up_bytes_1min_y', 'up_bytes_2min_y', 'up_bytes_3min_y', 'up_bytes_4min_y', 'up_bytes_5min_y',
            'up_bytes_1min_x', 'up_bytes_2min_x', 'up_bytes_3min_x', 'up_bytes_4min_x', 'up_bytes_5min_x',
            'up_packet_1max_y', 'up_packet_2max_y', 'up_packet_3max_y', 'up_packet_4max_y', 'up_packet_5max_y',
            'up_packet_1max_x', 'up_packet_2max_x', 'up_packet_3max_x', 'up_packet_4max_x', 'up_packet_5max_x',
            'up_packet_1min_y', 'up_packet_2min_y', 'up_packet_3min_y', 'up_packet_4min_y', 'up_packet_5min_y',
            'up_packet_1min_x', 'up_packet_2min_x', 'up_packet_3min_x', 'up_packet_4min_x', 'up_packet_5min_x',

            'down_bytes_mean', 'down_bytes_median', 'down_bytes_std', 'down_bytes_var', 'down_bytes_skew', 'down_bytes_kurt',
            'down_bytes_perc25', 'down_bytes_perc50', 'down_bytes_perc75', 'down_bytes_perc90',
            'down_bytes_silences', 'down_bytes_silence_mean', 'down_bytes_longest_silence', 'down_bytes_shortest_silence',
            'down_packet_mean', 'down_packet_median', 'down_packet_std', 'down_packet_var', 'down_packet_skew', 'down_packet_kurt',
            'down_packet_perc25', 'down_packet_perc50', 'down_packet_perc75', 'down_packet_perc90',
            'down_packet_silences', 'down_packet_silence_mean', 'down_packet_longest_silence', 'down_packet_shortest_silence',
            'down_bytes_1max_y', 'down_bytes_2max_y', 'down_bytes_3max_y', 'down_bytes_4max_y', 'down_bytes_5max_y',
            'down_bytes_1max_x', 'down_bytes_2max_x', 'down_bytes_3max_x', 'down_bytes_4max_x', 'down_bytes_5max_x',
            'down_bytes_1min_y', 'down_bytes_2min_y', 'down_bytes_3min_y', 'down_bytes_4min_y', 'down_bytes_5min_y',
            'down_bytes_1min_x', 'down_bytes_2min_x', 'down_bytes_3min_x', 'down_bytes_4min_x', 'down_bytes_5min_x',
            'down_packet_1max_y', 'down_packet_2max_y', 'down_packet_3max_y', 'down_packet_4max_y', 'down_packet_5max_y',
            'down_packet_1max_x', 'down_packet_2max_x', 'down_packet_3max_x', 'down_packet_4max_x', 'down_packet_5max_x',
            'down_packet_1min_y', 'down_packet_2min_y', 'down_packet_3min_y', 'down_packet_4min_y', 'down_packet_5min_y',
            'down_packet_1min_x', 'down_packet_2min_x', 'down_packet_3min_x', 'down_packet_4min_x', 'down_packet_5min_x',
            'label'
        ]
    
df = pd.DataFrame(samples, columns=names)

df

In [ ]:
outdir = 'csv/'
outname =  'all_30s_01s_128.csv'
if not os.path.exists(outdir):
    os.mkdir(outdir)
df.to_csv(os.path.join(outdir, outname), sep=',', encoding='utf-8')